In [1]:
# # This Python 3 environment comes with many helpful analytics libraries installed
# # It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# # For example, here's several helpful packages to load

# import numpy as np # linear algebra
# import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# # Input data files are available in the read-only "../input/" directory
# # For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

# import os
# for dirname, _, filenames in os.walk('/kaggle/input'):
#     for filename in filenames:
#         print(os.path.join(dirname, filename))

# # You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# # You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

In [2]:
!pip install music21

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 22.9/22.9 MB 56.7 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.4/199.4 kB 10.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.2/46.2 kB 1.8 MB/s eta 0:00:00


In [3]:
!pip install tiktoken

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 17.1 MB/s eta 0:00:00a 0:00:01


In [4]:
try:
    import midi2audio
except:
    !pip install midi2audio
    !sudo apt-get update
    !sudo apt-get install fluidsynth -y

Get:1 https://packages.cloud.google.com/apt gcsfuse-focal InRelease [1227 B]
Get:2 http://security.ubuntu.com/ubuntu focal-security InRelease [128 kB]      
Hit:3 http://archive.ubuntu.com/ubuntu focal InRelease                         
Get:4 https://packages.cloud.google.com/apt cloud-sdk InRelease [1618 B]       
Get:5 http://archive.ubuntu.com/ubuntu focal-updates InRelease [128 kB]        
Get:6 https://packages.cloud.google.com/apt gcsfuse-focal/main amd64 Packages [28.6 kB]
Get:7 https://packages.cloud.google.com/apt cloud-sdk/main all Packages [1582 kB]
Get:8 http://archive.ubuntu.com/ubuntu focal-backports InRelease [128 kB]      
Get:9 http://security.ubuntu.com/ubuntu focal-security/multiverse amd64 Packages [30.9 kB]
Get:10 https://packages.cloud.google.com/apt cloud-sdk/main amd64 Packages [3428 kB]
Get:11 http://security.ubuntu.com/ubuntu focal-security/restricted amd64 Packages [4137 kB]
Get:12 http://archive.ubuntu.com/ubuntu focal-updates/multiverse amd64 Packages [33.5

In [21]:
from importlib.metadata import version
import re
from midi2audio import FluidSynth
import IPython
from IPython.display import Image, Audio

pkgs = [
    "tiktoken",    # Tokenizer
    "torch",       # Deep learning library
]
for p in pkgs:
    print(f"{p} version: {version(p)}")

tiktoken version: 0.8.0
torch version: 2.4.0+cpu


In [6]:
from pathlib import Path

finetuned_model_path = Path("/kaggle/input/gpt-2-music-generator-model/gpt2-medium355M-sft_midi_5.pth")
if not finetuned_model_path.exists():
    print(
        f"Could not find '{finetuned_model_path}'.\n"
    )

In [7]:
# import module we'll need to import our custom module
from shutil import copyfile

# copy our file into the working directory (make sure it has .py suffix)
copyfile(src = "/kaggle/input/gpt-model-by-s.raschka/pytorch/default/1/previous_chapters.py", dst = "/kaggle/working/gpt_model.py")
copyfile(src = "/kaggle/input/miditokenizerv1/MidiTokenizerV1.py", dst = "/kaggle/working/MidiTokenizerV1.py")
copyfile(src = "/kaggle/input/miditokenizerv1/music_vocab.pkl", dst = "/kaggle/working/music_vocab.pkl")

'/kaggle/working/music_vocab.pkl'

In [8]:
from gpt_model import GPTModel

In [9]:
BASE_CONFIG = {
    "vocab_size": 54,     # Vocabulary size
    "context_length": 1024,  # Context length
    "drop_rate": 0.0,        # Dropout rate
    "qkv_bias": True         # Query-key-value bias
}

model_configs = {
    "gpt2-small (124M)": {"emb_dim": 768, "n_layers": 12, "n_heads": 12},
    "gpt2-medium (355M)": {"emb_dim": 1024, "n_layers": 24, "n_heads": 16},
    "gpt2-large (774M)": {"emb_dim": 1280, "n_layers": 36, "n_heads": 20},
    "gpt2-xl (1558M)": {"emb_dim": 1600, "n_layers": 48, "n_heads": 25},
}

CHOOSE_MODEL = "gpt2-medium (355M)"

BASE_CONFIG.update(model_configs[CHOOSE_MODEL])

# Initialize base model
model = GPTModel(BASE_CONFIG)

In [10]:
import torch

torch.manual_seed(123)

model.tok_emb = torch.nn.Embedding(BASE_CONFIG["vocab_size"], BASE_CONFIG["emb_dim"])

In [11]:
torch.manual_seed(123)

model.out_head = torch.nn.Linear(in_features=BASE_CONFIG["emb_dim"], out_features = BASE_CONFIG["vocab_size"], bias = False)

In [12]:
# print(model)

In [13]:
# Then load pretrained weights
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
model.load_state_dict(torch.load("/kaggle/input/gpt-2-music-generator-model/gpt2-medium355M-sft_midi_5.pth", map_location=device, weights_only=True))
model.to(device)
model.eval();

In [14]:
import pickle
# Load the dictionary from the .pkl file
with open('/kaggle/working/music_vocab.pkl', 'rb') as f:
    vocab = pickle.load(f)

# Check the loaded dictionary
print(vocab)

{'45': 0, '46': 1, '47': 2, '48': 3, '49': 4, '50': 5, '51': 6, '52': 7, '53': 8, '54': 9, '55': 10, '56': 11, '57': 12, '58': 13, '59': 14, '60': 15, '61': 16, '62': 17, '63': 18, '64': 19, '65': 20, '66': 21, '67': 22, '68': 23, '69': 24, '70': 25, '71': 26, '72': 27, '73': 28, '74': 29, '75': 30, '76': 31, '77': 32, '78': 33, '79': 34, '80': 35, '81': 36, '82': 37, '83': 38, '84': 39, '85': 40, '86': 41, '87': 42, '88': 43, '89': 44, '90': 45, '91': 46, '92': 47, '93': 48, '94': 49, '95': 50, '96': 51, '<|endoftext|>': 52, '<|unk|>': 53}


In [15]:
class MidiTokenizerV1:
    def __init__(self, vocab):
        self.str_to_int = vocab
        self.int_to_str = { i:s for s,i in vocab.items()}

    def encode(self, text):
        preprocessed = re.split(r'(\s)', text)
        preprocessed = [item.strip() for item in preprocessed if item.strip()]
        preprocessed = [
            item if item in self.str_to_int 
            else "<|unk|>" for item in preprocessed
        ]

        ids = [self.str_to_int[s] for s in preprocessed]
        return ids

    def decode(self, ids):
        text = " ".join([self.int_to_str[i] for i in ids])
        return text

tokenizer = MidiTokenizerV1(vocab)

In [16]:
from music21 import stream, note

def pitch_sequence_to_midi(pitch_sequence, output_midi_file="output.mid", note_duration=1.0):
    """
    Converts a pitch sequence into a MIDI file.

    Args:
        pitch_sequence (str): A string of space-separated pitch values (e.g., "67 66 67").
        output_midi_file (str): Path to save the resulting MIDI file.
        note_duration (float): Duration for each note (in quarter lengths).

    Returns:
        None: The function saves the MIDI file to the specified path.
    """
    # Parse the pitch sequence into a list of integers
    pitches = [int(p) for p in pitch_sequence.split() if p != "<|endoftext|>"]

    # pitches = list(map(int, pitch_sequence.split()))
    
    # Create a music21 Stream to hold the notes
    midi_stream = stream.Stream()

    for pitch in pitches:
        # Create a Note object for each pitch
        new_note = note.Note(pitch)
        new_note.quarterLength = note_duration  # Assign duration
        midi_stream.append(new_note)

    # Save the stream as a MIDI file
    midi_stream.write("midi", fp=output_midi_file)
    print(f"MIDI file saved as {output_midi_file}")

# Example usage
# pitch_sequence = notes_text
# pitch_sequence_to_midi(pitch_sequence, output_midi_file="pitch_sequence_output.mid")


In [17]:
def notes_to_pitch(note_string):
    """
    Translates a string of musical notes into a string of MIDI pitch numbers.

    Parameters:
    note_string (str): A space-separated string of musical notes (e.g., "C4 D#4 F5").

    Returns:
    str: A space-separated string of MIDI pitch numbers (e.g., "60 63 77").
    """
    # Define the base note mapping
    note_to_semitone = {
        'C': 0, 'C#': 1, 'D': 2, 'D#': 3, 'E': 4,
        'F': 5, 'F#': 6, 'G': 7, 'G#': 8, 'A': 9,
        'A#': 10, 'B': 11
    }

    midi_pitches = []

    # Split the input string into individual notes
    notes = note_string.split()

    for note in notes:
        # Extract the base note and the octave
        base_note = note[:-1]
        octave = int(note[-1])

        if base_note in note_to_semitone:
            # Calculate MIDI pitch
            semitone = note_to_semitone[base_note]
            midi_pitch = (octave + 1) * 12 + semitone
            midi_pitches.append(str(midi_pitch))
        else:
            raise ValueError(f"Invalid note: {note}")

    # Return MIDI pitches as a space-separated string
    return " ".join(midi_pitches)

In [18]:
def generate(model, idx, max_new_tokens, context_size, temperature=0.0, top_k=None, eos_id=None):

    # For-loop is the same as before: Get logits, and only focus on last time step
    for _ in range(max_new_tokens):
        idx_cond = idx[:, -context_size:]
        with torch.no_grad():
            logits = model(idx_cond)
        logits = logits[:, -1, :]

        # New: Filter logits with top_k sampling
        if top_k is not None:
            # Keep only top_k values
            top_logits, _ = torch.topk(logits, top_k)
            min_val = top_logits[:, -1]
            logits = torch.where(logits < min_val, torch.tensor(float("-inf")).to(logits.device), logits)

        # New: Apply temperature scaling
        if temperature > 0.0:
            logits = logits / temperature

            # Apply softmax to get probabilities
            probs = torch.softmax(logits, dim=-1)  # (batch_size, context_len)

            # Sample from the distribution
            idx_next = torch.multinomial(probs, num_samples=1)  # (batch_size, 1)

        # Otherwise same as before: get idx of the vocab entry with the highest logits value
        else:
            idx_next = torch.argmax(logits, dim=-1, keepdim=True)  # (batch_size, 1)

        if idx_next == eos_id:  # Stop generating early if end-of-sequence token is encountered and eos_id is specified
            break

        # Same as before: append sampled index to the running sequence
        idx = torch.cat((idx, idx_next), dim=1)  # (batch_size, num_tokens+1)

    return idx

In [19]:
torch.manual_seed(123)

def text_to_token_ids(text, tokenizer):
    encoded = tokenizer.encode(text)
    encoded_tensor = torch.tensor(encoded).unsqueeze(0) # add batch dimension
    return encoded_tensor

def token_ids_to_text(token_ids, tokenizer):
    flat = token_ids.squeeze(0) # remove batch dimension
    return tokenizer.decode(flat.tolist())

start_context = notes_to_pitch(input("Enter a string of musical notes (e.g. G#4 F#4 E4 C#4 E4 F#4 G#4):"))

token_ids = generate(
    model=model,
    idx=text_to_token_ids(start_context, tokenizer).to(device),
    max_new_tokens=100,
    context_size=BASE_CONFIG["context_length"],
    top_k=5,
    temperature=1.2,
    eos_id= 52
)

notes_text=token_ids_to_text(token_ids, tokenizer)

pitch_sequence = notes_text
pitch_sequence_to_midi(pitch_sequence, output_midi_file="pitch_sequence_output.mid")
# print(notes_text)

Enter a string of musical notes (e.g. G#4 F#4 E4 C#4 E4 F#4 G#4): G#4 F#4 E4 C#4 E4 F#4 G#4


MIDI file saved as pitch_sequence_output.mid


In [22]:
fs = FluidSynth()
file = '/kaggle/working/pitch_sequence_output.mid'
fs.midi_to_audio(file, 'output.wav')
IPython.display.Audio("output.wav") 

Parameter '/root/.fluidsynth/default_sound_font.sf2' not a SoundFont or MIDI file or error occurred identifying it.


FluidSynth runtime version 2.1.1
Copyright (C) 2000-2020 Peter Hanappe and others.
Distributed under the LGPL license.
SoundFont(R) is a registered trademark of E-mu Systems, Inc.

Rendering audio to file 'output.wav'..
